In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/large-license-plate-dataset/labels/val.cache
/kaggle/input/large-license-plate-dataset/labels/train.cache
/kaggle/input/large-license-plate-dataset/labels/val/790e3002a96d85a5.txt
/kaggle/input/large-license-plate-dataset/labels/val/688f112cf2794184.txt
/kaggle/input/large-license-plate-dataset/labels/val/ab2cff14a7b52e36.txt
/kaggle/input/large-license-plate-dataset/labels/val/6687bdff027c5b55.txt
/kaggle/input/large-license-plate-dataset/labels/val/0dee0d9dfd8e3cfa.txt
/kaggle/input/large-license-plate-dataset/labels/val/a5aee0ff39881591.txt
/kaggle/input/large-license-plate-dataset/labels/val/5d17512ab9c09db4.txt
/kaggle/input/large-license-plate-dataset/labels/val/62bd4774a7c7f8ea.txt
/kaggle/input/large-license-plate-dataset/labels/val/d8cc7fd0fb4f8c71.txt
/kaggle/input/large-license-plate-dataset/labels/val/2c77e85396415e64.txt
/kaggle/input/large-license-plate-dataset/labels/val/5728b902e329d168.txt
/kaggle/input/large-license-plate-dataset/labels/val/8bc9bcf9e0b17

In [2]:
import wandb

wandb.login(key="b7fbf19e34af4a6f2b90b6b17e088e7a7a1c832b")

wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [3]:
wandb.init(
    # set the wandb project where this run will be logged
    project="YOLO_object_detections",

)

wandb: Currently logged in as: ragabhassan716 (translations_smsm). Use `wandb login --relogin` to force relogin
wandb: wandb version 0.17.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.16.6
wandb: Run data is saved locally in /kaggle/working/wandb/run-20240512_230812-vkfnvukp
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run visionary-water-6
wandb: ⭐️ View project at https://wandb.ai/translations_smsm/YOLO_object_detections
wandb: 🚀 View run at https://wandb.ai/translations_smsm/YOLO_object_detections/runs/vkfnvukp


In [4]:
import cv2
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import os
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split



import torch


In [5]:
x=os.listdir("/kaggle/input/large-license-plate-dataset/images/train")
len(x)

25470

In [6]:
y=os.listdir("/kaggle/input/large-license-plate-dataset/labels/val")
len(y)

1073

In [7]:
25470 /6000

4.245

In [8]:
!git clone https://github.com/ultralytics/yolov5.git


Cloning into 'yolov5'...
remote: Enumerating objects: 16607, done.
remote: Counting objects: 100% (85/85), done.
remote: Compressing objects: 100% (61/61), done.
remote: Total 16607 (delta 45), reused 51 (delta 24), pack-reused 16522
Receiving objects: 100% (16607/16607), 15.14 MiB | 28.76 MiB/s, done.
Resolving deltas: 100% (11398/11398), done.


In [9]:
%cd yolov5
!pip install -U -r requirements.txt

/kaggle/working/yolov5
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.6/60.6 kB 1.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.7/40.7 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 3.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 65.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 72.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 288.2/288.2 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.6/38.6 MB 37.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 779.1/779.1 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 59.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 55.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━

In [10]:
%cd /kaggle/working/
! mkdir yolo_data
%cd yolo_data
! mkdir train

/kaggle/working
/kaggle/working/yolo_data


In [11]:
%cd train
#! mkdir labels
#! mkdir images

/kaggle/working/yolo_data/train


# find a way to copy files from input to wd

In [12]:
! cp -r /kaggle/input/large-license-plate-dataset/labels/train /kaggle/working/yolo_data/train/labels

In [13]:
! cp -r /kaggle/input/large-license-plate-dataset/images/train /kaggle/working/yolo_data/train/images

In [14]:
%cd /kaggle/working/yolo_data

/kaggle/working/yolo_data


In [15]:
!pwd

/kaggle/working/yolo_data


In [16]:
! mkdir val

In [17]:
%cd val
!pwd

/kaggle/working/yolo_data/val
/kaggle/working/yolo_data/val


In [18]:
! cp -r /kaggle/input/large-license-plate-dataset/images/val /kaggle/working/yolo_data/val/images

In [19]:
! cp -r /kaggle/input/large-license-plate-dataset/labels/val /kaggle/working/yolo_data/val/labels

In [20]:
%cd /kaggle/working/yolo_data

/kaggle/working/yolo_data


In [21]:
!pwd

/kaggle/working/yolo_data


In [22]:
! mkdir test

In [23]:
%cd test

/kaggle/working/yolo_data/test


In [24]:
!pwd

/kaggle/working/yolo_data/test


In [25]:
! cp -r /kaggle/input/large-license-plate-dataset/labels/test /kaggle/working/yolo_data/test/labels

In [26]:
! cp -r /kaggle/input/large-license-plate-dataset/images/test /kaggle/working/yolo_data/test/images

In [27]:
%cd /kaggle/working/

/kaggle/working


In [28]:
!pwd

/kaggle/working


In [29]:
!echo "train: /kaggle/working/yolo_data/train" > data.yaml
!echo "val: /kaggle/working/yolo_data/val" >> data.yaml
!echo "test: /kaggle/working/yolo_data/test" >> data.yaml
!echo "nc: 1" >> data.yaml
!echo "names: ['license_plate']" >> data.yaml


In [30]:
file_path = "/kaggle/working/yolov5/models/yolov5s.yaml"

try:
    with open(file_path, 'r') as file:
        content = file.read()
        print(content)
except FileNotFoundError:
    print("File not found.")


# YOLOv5 🚀 by Ultralytics, AGPL-3.0 license

# Parameters
nc: 80 # number of classes
depth_multiple: 0.33 # model depth multiple
width_multiple: 0.50 # layer channel multiple
anchors:
  - [10, 13, 16, 30, 33, 23] # P3/8
  - [30, 61, 62, 45, 59, 119] # P4/16
  - [116, 90, 156, 198, 373, 326] # P5/32

# YOLOv5 v6.0 backbone
backbone:
  # [from, number, module, args]
  [
    [-1, 1, Conv, [64, 6, 2, 2]], # 0-P1/2
    [-1, 1, Conv, [128, 3, 2]], # 1-P2/4
    [-1, 3, C3, [128]],
    [-1, 1, Conv, [256, 3, 2]], # 3-P3/8
    [-1, 6, C3, [256]],
    [-1, 1, Conv, [512, 3, 2]], # 5-P4/16
    [-1, 9, C3, [512]],
    [-1, 1, Conv, [1024, 3, 2]], # 7-P5/32
    [-1, 3, C3, [1024]],
    [-1, 1, SPPF, [1024, 5]], # 9
  ]

# YOLOv5 v6.0 head
head: [
    [-1, 1, Conv, [512, 1, 1]],
    [-1, 1, nn.Upsample, [None, 2, "nearest"]],
    [[-1, 6], 1, Concat, [1]], # cat backbone P4
    [-1, 3, C3, [512, False]], # 13

    [-1, 1, Conv, [256, 1, 1]],
    [-1, 1, nn.Upsample, [None, 2, "nearest"]],
    [[-1, 

In [31]:
file_path = "/kaggle/working/yolov5/models/yolov5s.yaml"

try:
    with open(file_path, 'r') as file:
        content = file.read()

    # Make your edits to the content
    # For example, let's say you want to replace all occurrences of 'old_text' with 'new_text'
    content = content.replace('nc: 80 # number of classes', 'nc: 1 # number of classes')

    # Open the file in write mode to overwrite the existing content
    with open(file_path, 'w') as file:
        file.write(content)
        print("File edited successfully.")
except FileNotFoundError:
    print("File not found.")


File edited successfully.


In [32]:
file_path = "/kaggle/working/yolov5/models/yolov5s.yaml"

try:
    with open(file_path, 'r') as file:
        content = file.read()
        print(content)
except FileNotFoundError:
    print("File not found.")


# YOLOv5 🚀 by Ultralytics, AGPL-3.0 license

# Parameters
nc: 1 # number of classes
depth_multiple: 0.33 # model depth multiple
width_multiple: 0.50 # layer channel multiple
anchors:
  - [10, 13, 16, 30, 33, 23] # P3/8
  - [30, 61, 62, 45, 59, 119] # P4/16
  - [116, 90, 156, 198, 373, 326] # P5/32

# YOLOv5 v6.0 backbone
backbone:
  # [from, number, module, args]
  [
    [-1, 1, Conv, [64, 6, 2, 2]], # 0-P1/2
    [-1, 1, Conv, [128, 3, 2]], # 1-P2/4
    [-1, 3, C3, [128]],
    [-1, 1, Conv, [256, 3, 2]], # 3-P3/8
    [-1, 6, C3, [256]],
    [-1, 1, Conv, [512, 3, 2]], # 5-P4/16
    [-1, 9, C3, [512]],
    [-1, 1, Conv, [1024, 3, 2]], # 7-P5/32
    [-1, 3, C3, [1024]],
    [-1, 1, SPPF, [1024, 5]], # 9
  ]

# YOLOv5 v6.0 head
head: [
    [-1, 1, Conv, [512, 1, 1]],
    [-1, 1, nn.Upsample, [None, 2, "nearest"]],
    [[-1, 6], 1, Concat, [1]], # cat backbone P4
    [-1, 3, C3, [512, False]], # 13

    [-1, 1, Conv, [256, 1, 1]],
    [-1, 1, nn.Upsample, [None, 2, "nearest"]],
    [[-1, 4

In [33]:
!python -m torch.distributed.run --nproc_per_node=2 --master_port 1 /kaggle/working/yolov5/train.py --img 2000 --batch 16 --epochs 3 --data /kaggle/working/data.yaml --cfg /kaggle/working/yolov5/models/yolov5s.yaml --weights yolov5s.pt   --device 0,1


wandb: WARNING ⚠️ wandb is deprecated and will be removed in a future release. See supported integrations at https://github.com/ultralytics/yolov5#integrations.
2024-05-12 23:20:07.546275: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-12 23:20:07.546275: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-12 23:20:07.546347: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-12 23:20:07.546411: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been register

In [34]:
!python /kaggle/working/yolov5/val.py  --img 100 --data /kaggle/working/data.yaml --weights yolov5/runs/train/exp2/weights/best.pt --task test


val: data=/kaggle/working/data.yaml, weights=['yolov5/runs/train/exp2/weights/best.pt'], batch_size=32, imgsz=100, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=yolov5/runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v7.0-311-g28e06aa3 Python-3.10.13 torch-2.3.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

Fusing layers... 
YOLOv5s summary: 157 layers, 7012822 parameters, 0 gradients, 15.8 GFLOPs
WARNING ⚠️ --img-size 100 must be multiple of max stride 32, updating to 128
test: Scanning /kaggle/working/yolo_data/test/labels... 386 images, 0 background
test: New cache created: /kaggle/working/yolo_data/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   
                   all        386        512      0.411      0.203      0.203     0.0735
Speed: 0.0ms pre-process, 1.6ms inferen

In [35]:
!python /kaggle/working/yolov5/detect.py --source /kaggle/working/yolo_data/test/images/343326e127297379.jpg --weights yolov5/runs/train/exp2/weights/best.pt --conf 0.4


detect: weights=['yolov5/runs/train/exp2/weights/best.pt'], source=/kaggle/working/yolo_data/test/images/343326e127297379.jpg, data=yolov5/data/coco128.yaml, imgsz=[640, 640], conf_thres=0.4, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=yolov5/runs/detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5 🚀 v7.0-311-g28e06aa3 Python-3.10.13 torch-2.3.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

Fusing layers... 
YOLOv5s summary: 157 layers, 7012822 parameters, 0 gradients, 15.8 GFLOPs
image 1/1 /kaggle/working/yolo_data/test/images/343326e127297379.jpg: 448x640 1 license_plate, 58.4ms
Speed: 0.5ms pre-process, 58.4ms inference, 527.3ms NMS per image at shape (1, 3, 640, 640)
Results saved to yolov5/runs/detect/exp
